<img src="https://github.com/hernancontigiani/ceia_memorias_especializacion/raw/master/Figures/logoFIUBA.jpg" width="500" align="center">


# Procesamiento de lenguaje natural
## Custom embedddings con Gensim



In [26]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

import multiprocessing
from gensim.models import Word2Vec

### Datos
Utilizaremos un dataset con fake-news,

In [27]:
import gensim.downloader as api

info = api.info()  # show info about available models/datasets

In [28]:
dataset_path=api.load("fake-news",return_path=True)
dataset_path

'C:\\Users\\santi/gensim-data\\fake-news\\fake-news.gz'

In [29]:
df = pd.read_csv('C:\\Users\\santi\\gensim-data\\fake-news\\fake.csv', sep=',')
df.head()

uuid  ord_in_thread  \
0  6a175f46bcd24d39b3e962ad0f29936721db70db              0   
1  2bdc29d12605ef9cf3f09f9875040a7113be5d5b              0   
2  c70e149fdd53de5e61c29281100b9de0ed268bc3              0   
3  7cf7c15731ac2a116dd7f629bd57ea468ed70284              0   
4  0206b54719c7e241ffe0ad4315b808290dbe6c0f              0   

                 author                      published  \
0     Barracuda Brigade  2016-10-26T21:41:00.000+03:00   
1  reasoning with facts  2016-10-29T08:47:11.259+03:00   
2     Barracuda Brigade  2016-10-31T01:41:49.479+02:00   
3                Fed Up  2016-11-01T05:22:00.000+02:00   
4                Fed Up  2016-11-01T21:56:00.000+02:00   

                                               title  \
0  Muslims BUSTED: They Stole Millions In Gov’t B...   
1  Re: Why Did Attorney General Loretta Lynch Ple...   
2  BREAKING: Weiner Cooperating With FBI On Hilla...   
3  PIN DROP SPEECH BY FATHER OF DAUGHTER Kidnappe...   
4  FANTASTIC! TRUMP'S 7 POINT PLAN To Reform Heal...   

                                                text language  \
0  Print They should pay all the back all the mon...  english   
1  Why Did Attorney General Loretta Lynch Plead T...  english   
2  Red State : \nFox News Sunday reported this mo...  english   
3  Email Kayla Mueller was a prisoner and torture...  english   
4  Email HEALTHCARE REFORM TO MAKE AMERICA GREAT ...  english   

                         crawled             site_url country  domain_rank  \
0  2016-10-27T01:49:27.168+03:00  100percentfedup.com      US      25689.0   
1  2016-10-29T08:47:11.259+03:00  100percentfedup.com      US      25689.0   
2  2016-10-31T01:41:49.479+02:00  100percentfedup.com      US      25689.0   
3  2016-11-01T15:46:26.304+02:00  100percentfedup.com      US      25689.0   
4  2016-11-01T23:59:42.266+02:00  100percentfedup.com      US      25689.0   

                                        thread_title  spam_score  \
0  Muslims BUSTED: They Stole Millions In Gov’t B...       0.000   
1  Re: Why Did Attorney General Loretta Lynch Ple...       0.000   
2  BREAKING: Weiner Cooperating With FBI On Hilla...       0.000   
3  PIN DROP SPEECH BY FATHER OF DAUGHTER Kidnappe...       0.068   
4  FANTASTIC! TRUMP'S 7 POINT PLAN To Reform Heal...       0.865   

                                        main_img_url  replies_count  \
0  http://bb4sp.com/wp-content/uploads/2016/10/Fu...              0   
1  http://bb4sp.com/wp-content/uploads/2016/10/Fu...              0   
2  http://bb4sp.com/wp-content/uploads/2016/10/Fu...              0   
3  http://100percentfedup.com/wp-content/uploads/...              0   
4  http://100percentfedup.com/wp-content/uploads/...              0   

   participants_count  likes  comments  shares  type  
0                   1      0         0       0  bias  
1                   1      0         0       0  bias  
2                   1      0         0       0  bias  
3                   0      0         0       0  bias  
4                   0      0         0       0  bias

In [30]:
print("Cantidad de documentos:", df.shape[0])

Cantidad de documentos: 12999


### 1 - Preprocesamiento

In [31]:
df=df["text"]
df

0        Print They should pay all the back all the mon...
1        Why Did Attorney General Loretta Lynch Plead T...
2        Red State : \nFox News Sunday reported this mo...
3        Email Kayla Mueller was a prisoner and torture...
4        Email HEALTHCARE REFORM TO MAKE AMERICA GREAT ...
                               ...                        
12994    It DOES allow you to put a dog face on top of ...
12995    Wait till you see what happens to the valuatio...
12996    I'm waiting for the one that puts a pussy on m...
12997    $4 Billion even after they are known to be kee...
12998    of course - how else would they disceminate te...
Name: text, Length: 12999, dtype: object

In [36]:
from keras.preprocessing.text import text_to_word_sequence
import pandas as pd
import numpy as np

sentence_tokens = []

# Recorrer la serie y transformar cada elemento en una secuencia de palabras
for sentence in df:
    if isinstance(sentence, str):  # Verificar que el elemento no sea NaN
        sentence_tokens.append(text_to_word_sequence(sentence))
    else:
        # Si el elemento es NaN, puedes tratarlo como un string vacío o hacer otra acción deseada
        sentence_tokens.append([])  # Por ejemplo, agregar una lista vacía

# Convertir la lista de tokens en una nueva columna del DataFrame si lo deseas
df["tokens"] = sentence_tokens


In [38]:
# Demos un vistazo
sentence_tokens

[['print',
  'they',
  'should',
  'pay',
  'all',
  'the',
  'back',
  'all',
  'the',
  'money',
  'plus',
  'interest',
  'the',
  'entire',
  'family',
  'and',
  'everyone',
  'who',
  'came',
  'in',
  'with',
  'them',
  'need',
  'to',
  'be',
  'deported',
  'asap',
  'why',
  'did',
  'it',
  'take',
  'two',
  'years',
  'to',
  'bust',
  'them',
  'here',
  'we',
  'go',
  'again',
  '…another',
  'group',
  'stealing',
  'from',
  'the',
  'government',
  'and',
  'taxpayers',
  'a',
  'group',
  'of',
  'somalis',
  'stole',
  'over',
  'four',
  'million',
  'in',
  'government',
  'benefits',
  'over',
  'just',
  '10',
  'months',
  'we’ve',
  'reported',
  'on',
  'numerous',
  'cases',
  'like',
  'this',
  'one',
  'where',
  'the',
  'muslim',
  'refugees',
  'immigrants',
  'commit',
  'fraud',
  'by',
  'scamming',
  'our',
  'system…it’s',
  'way',
  'out',
  'of',
  'control',
  'more',
  'related'],
 ['why',
  'did',
  'attorney',
  'general',
  'loretta',
  '

### 2 - Crear los vectores (word2vec)

In [40]:
from gensim.models.callbacks import CallbackAny2Vec
# Durante el entrenamiento gensim por defecto no informa el "loss" en cada época
# Sobrecargamos el callback para poder tener esta información
class callback(CallbackAny2Vec):
    """
    Callback to print loss after each epoch
    """
    def __init__(self):
        self.epoch = 0

    def on_epoch_end(self, model):
        loss = model.get_latest_training_loss()
        if self.epoch == 0:
            print('Loss after epoch {}: {}'.format(self.epoch, loss))
        else:
            print('Loss after epoch {}: {}'.format(self.epoch, loss- self.loss_previous_step))
        self.epoch += 1
        self.loss_previous_step = loss

In [41]:
# Crearmos el modelo generador de vectores
# En este caso utilizaremos la estructura modelo Skipgram
w2v_model = Word2Vec(min_count=5,    # frecuencia mínima de palabra para incluirla en el vocabulario
                     window=2,       # cant de palabras antes y desp de la predicha
                     vector_size=300,       # dimensionalidad de los vectores 
                     negative=20,    # cantidad de negative samples... 0 es no se usa
                     workers=1,      # si tienen más cores pueden cambiar este valor
                     sg=1)           # modelo 0:CBOW  1:skipgram

In [42]:
# Obtener el vocabulario con los tokens
w2v_model.build_vocab(sentence_tokens)

In [43]:
# Cantidad de filas/docs encontradas en el corpus
print("Cantidad de docs en el corpus:", w2v_model.corpus_count)

Cantidad de docs en el corpus: 12999


In [44]:
# Cantidad de words encontradas en el corpus
print("Cantidad de words distintas en el corpus:", len(w2v_model.wv.index_to_key))

Cantidad de words distintas en el corpus: 48614


### 3 - Entrenar el modelo generador

In [45]:
# Entrenamos el modelo generador de vectores
# Utilizamos nuestro callback
w2v_model.train(sentence_tokens,
                 total_examples=w2v_model.corpus_count,
                 epochs=20,
                 compute_loss = True,
                 callbacks=[callback()]
                 )

Loss after epoch 0: 50342156.0
Loss after epoch 1: 24906052.0
Loss after epoch 2: 12665440.0
Loss after epoch 3: 12480896.0
Loss after epoch 4: 12283400.0
Loss after epoch 5: 12028184.0
Loss after epoch 6: 9511600.0
Loss after epoch 7: 0.0
Loss after epoch 8: 0.0
Loss after epoch 9: 0.0
Loss after epoch 10: 0.0
Loss after epoch 11: 0.0
Loss after epoch 12: 0.0


KeyboardInterrupt: 

### 4 - Ensayar

In [50]:
# Palabras que MÁS se relacionan con...:
w2v_model.wv.most_similar(positive=["love"], topn=10)

[('equanimity', 0.46229150891304016),
 ('compassion', 0.4617463946342468),
 ('generosity', 0.4306759536266327),
 ('“love”', 0.41561126708984375),
 ('means…', 0.41451314091682434),
 ('austen', 0.4116319417953491),
 ('togetherness', 0.411253422498703),
 ('benevolence', 0.41006171703338623),
 ('preacher62', 0.40920159220695496),
 ('pageants', 0.4078139364719391)]

In [51]:
# Palabras que MENOS se relacionan con...:
w2v_model.wv.most_similar(negative=["love"], topn=10)

[('вашей', 0.07574141770601273),
 ('bruce', 0.05815457925200462),
 ('engineered', 0.051425788551568985),
 ('hanjin', 0.04619342088699341),
 ('paramilitary', 0.04588676244020462),
 ('awogbade', 0.044119689613580704),
 ('iarc', 0.04294750094413757),
 ('robert', 0.04261580482125282),
 ('demolition', 0.03953228518366814),
 ('jason', 0.038729116320610046)]

In [52]:
# Palabras que MÁS se relacionan con...:
w2v_model.wv.most_similar(positive=["four"], topn=10)

[('three', 0.5721057653427124),
 ('five', 0.5397377014160156),
 ('two', 0.5223328471183777),
 ('eight', 0.5222485661506653),
 ('seven', 0.48310157656669617),
 ('six', 0.476423442363739),
 ('sixteen', 0.4582682251930237),
 ('814', 0.45394352078437805),
 ('sixty', 0.450347900390625),
 ('fifty', 0.44935765862464905)]

In [53]:
# Palabras que MÁS se relacionan con...:
w2v_model.wv.most_similar(positive=["money"], topn=5)

[('makin', 0.5494661331176758),
 ("taxpayers'", 0.4888565242290497),
 ('funds', 0.46578848361968994),
 ('“money', 0.45470499992370605),
 ('100’s', 0.45419418811798096)]

In [54]:
# Ensayar con una palabra que no está en el vocabulario:
w2v_model.wv.most_similar(negative=["diedaa"])

KeyError: "Key 'diedaa' not present in vocabulary"

### 5 - Visualizar agrupación de vectores

In [55]:
from sklearn.decomposition import IncrementalPCA    
from sklearn.manifold import TSNE                   
import numpy as np                                  

def reduce_dimensions(model):
    num_dimensions = 2  

    vectors = np.asarray(model.wv.vectors)
    labels = np.asarray(model.wv.index_to_key)  

    tsne = TSNE(n_components=num_dimensions, random_state=0)
    vectors = tsne.fit_transform(vectors)

    x_vals = [v[0] for v in vectors]
    y_vals = [v[1] for v in vectors]
    return x_vals, y_vals, labels

In [56]:
# Graficar los embedddings en 2D
import plotly.graph_objects as go
import plotly.express as px

x_vals, y_vals, labels = reduce_dimensions(w2v_model)

MAX_WORDS=200
fig = px.scatter(x=x_vals[:MAX_WORDS], y=y_vals[:MAX_WORDS], text=labels[:MAX_WORDS])
fig.show(renderer="colab") # esto para plotly en colab

### Alumno

- Crear sus propios vectores con Gensim basado en lo visto en clase con otro dataset.
- Probar términos de interés y explicar similitudes en el espacio de embeddings (sacar conclusiones entre palabras similitudes y diferencias).
- Graficarlos.
- Obtener conclusiones.